# Opening A New Mall In Singapore - Analysis

In this project, we aim to find out those places in Singapore where building a shopping mall would be the most viable choice, from the perspective of a property developer.

## 1. Importing the libraries
First, we import all the required libraries

In [1]:
import numpy as np # library to handle data in a vectorized manner

import pandas as pd # library for data analysis
pd.set_option("display.max_columns", None)
pd.set_option("display.max_rows", None)

import json # library to handle JSON files

from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import geocoder # to get coordinates

import requests # library to handle requests
from bs4 import BeautifulSoup # library to parse HTML and XML documents

from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

import folium # map rendering library
from urllib.request import urlopen

print("Libraries imported.")

Libraries imported.


## 2. Extracting Wikipedia data into a DataFrame
We need data regarding the subdivisions of Singapore to consider. I chose the Wikipedia page containing all the Singaporean postal codes and the general locations. Let's get the HTML of the webpage.

In [2]:
url="https://en.wikipedia.org/wiki/Postal_codes_in_Singapore"
html=urlopen(url)

Converting the html to a BeautifulSoup object so that we can parse the HTML to get what we need

In [3]:
soup=BeautifulSoup(html,'lxml')

We only require the table given in the webpage, which contains postal district, postal sector, and general location (this is the column we actually need). Therefore we extract only the table rows.

In [4]:
table_rows=soup.find_all('tr')

Remove the tags from the text and store the text in a list:


In [5]:
table=[]
for row in table_rows:
    listrows = str(row.find_all('td'))
    cleantext = BeautifulSoup(listrows, "lxml").get_text()
    table.append(cleantext)
print(table_rows)

[<tr>
<th>Postal district
</th>
<th>Postal sector<br/>(1st 2 digits of 6-digit postal codes)
</th>
<th>General location
</th></tr>, <tr>
<td>01
</td>
<td>01, 02, 03, 04, 05, 06
</td>
<td>Raffles Place, Cecil, Marina, People's Park
</td></tr>, <tr>
<td>02
</td>
<td>07, 08
</td>
<td>Anson, Tanjong Pagar
</td></tr>, <tr>
<td>03
</td>
<td>14, 15, 16
</td>
<td><a href="/wiki/Bukit_Merah" title="Bukit Merah">Bukit Merah</a>, <a href="/wiki/Queenstown,_Singapore" title="Queenstown, Singapore">Queenstown</a>, <a href="/wiki/Tiong_Bahru" title="Tiong Bahru">Tiong Bahru</a>
</td></tr>, <tr>
<td>04
</td>
<td>09, 10
</td>
<td>Telok Blangah, Harbourfront
</td></tr>, <tr>
<td>05
</td>
<td>11, 12, 13
</td>
<td>Pasir Panjang, Hong Leong Garden, Clementi New Town
</td></tr>, <tr>
<td>06
</td>
<td>17
</td>
<td>High Street, Beach Road (part)
</td></tr>, <tr>
<td>07
</td>
<td>18, 19
</td>
<td>Middle Road, Golden Mile
</td></tr>, <tr>
<td>08
</td>
<td>20, 21
</td>
<td><a href="/wiki/Little_India,_Singapore

Convert the list to a DataFrame


In [6]:
df=pd.DataFrame(table)
df.head(10)

0
0                                                 []
1  [01\n, 01, 02, 03, 04, 05, 06\n, Raffles Place...
2           [02\n, 07, 08\n, Anson, Tanjong Pagar\n]
3  [03\n, 14, 15, 16\n, Bukit Merah, Queenstown, ...
4    [04\n, 09, 10\n, Telok Blangah, Harbourfront\n]
5  [05\n, 11, 12, 13\n, Pasir Panjang, Hong Leong...
6     [06\n, 17\n, High Street, Beach Road (part)\n]
7       [07\n, 18, 19\n, Middle Road, Golden Mile\n]
8  [08\n, 20, 21\n, Little India, Farrer Park, Ja...
9  [09\n, 22, 23\n, Orchard, Cairnhill, River Val...

All the table values are in a single column. Let's split it.


In [7]:
df1=df[0].str.split('\n',expand=True)
df1

0  \
0                                                  []   
1                                                 [01   
2                                                 [02   
3                                                 [03   
4                                                 [04   
5                                                 [05   
6                                                 [06   
7                                                 [07   
8                                                 [08   
9                                                 [09   
10                                                [10   
11                                                [11   
12                                                [12   
13                                                [13   
14                                                [14   
15                                                [15   
16                                                [16   
17                                                [17   
18                                                [18   
19                                                [19   
20                                                [20   
21                                                [21   
22                                                [22   
23                                                [23   
24                                                [24   
25                                                [25   
26                                                [26   
27                                                [27   
28                                                [28   
29                                                 []   
30  [Ms. Tan Bee Soo16 Sandilands RoadSINGAPORE 54...   
31  [Mr. M. RajendranBlk 35 Mandalay Road # 13–37 ...   
32                                                 []   
33                                                  [   
34                                                  [   
35                                                  [   
36                                                  [   

                                                    1  \
0                                                None   
1                            , 01, 02, 03, 04, 05, 06   
2                                            , 07, 08   
3                                        , 14, 15, 16   
4                                            , 09, 10   
5                                        , 11, 12, 13   
6                                                , 17   
7                                            , 18, 19   
8                                            , 20, 21   
9                                            , 22, 23   
10                                   , 24, 25, 26, 27   
11                                       , 28, 29, 30   
12                                       , 31, 32, 33   
13                                   , 34, 35, 36, 37   
14                                   , 38, 39, 40, 41   
15                                   , 42, 43, 44, 45   
16                                       , 46, 47, 48   
17                                       , 49, 50, 81   
18                                           , 51, 52   
19                                   , 53, 54, 55, 82   
20                                           , 56, 57   
21                                           , 58, 59   
22                               , 60, 61, 62, 63, 64   
23                                   , 65, 66, 67, 68   
24                                       , 69, 70, 71   
25                                           , 72, 73   
26                                           , 77, 78   
27                                           , 75, 76   
28                                           , 79, 80   
29                                               None   
30  , name of addresseestreet number and namename ...   
31  , name of addresseeblock number and street nam...   
32  

Drop the unnecessary columns and rows

In [8]:
df1=df1.drop(df1.index[29:37],axis=0)
df1=df1.drop([0],axis=0)
df1=df1.drop(df1.iloc[:,3:51],axis=1)
df1=df1.drop(df1.iloc[:,0:2],axis=1)

In [9]:
df1=df1.reset_index(drop=True)
df1 = df1.T.reset_index(drop=True).T

In [10]:
df1.head()

0
0       , Raffles Place, Cecil, Marina, People's Park
1                              , Anson, Tanjong Pagar
2              , Bukit Merah, Queenstown, Tiong Bahru
3                       , Telok Blangah, Harbourfront
4   , Pasir Panjang, Hong Leong Garden, Clementi N...
5                    , High Street, Beach Road (part)
6                          , Middle Road, Golden Mile
7   , Little India, Farrer Park, Jalan Besar, Lave...
8                  , Orchard, Cairnhill, River Valley
9       , Ardmore, Bukit Timah, Holland Road, Tanglin
10                   , Watten Estate, Novena, Thomson
11                  , Balestier, Toa Payoh, Serangoon
12                             , Macpherson, Braddell
13                                   , Geylang, Eunos
14                    , Katong, Joo Chiat, Amber Road
15     , Bedok, Upper East Coast, Eastwood, Kew Drive
16                                   , Loyang, Changi
17                       , Simei, Tampines, Pasir Ris
18               , Serangoon Garden, Hougang, Punggol
19                               , Bishan, Ang Mo Kio
20     , Upper Bukit Timah, Clementi Park, Ulu Pandan
21                                     , Jurong, Tuas
22  , Hillview, Dairy Farm, Bukit Panjang, Choa Ch...
23                             , Lim Chu Kang, Tengah
24                     , Kranji, Woodgrove, Woodlands
25                        , Upper Thomson, Springleaf
26                                , Yishun, Sembawang
27                                          , Seletar

Stripping the commas and whitespaces from each row

In [11]:
df1[0]=df1[0].str.strip(',')
df1[0]=df1[0].str.strip(' ')
df1

0
0         Raffles Place, Cecil, Marina, People's Park
1                                Anson, Tanjong Pagar
2                Bukit Merah, Queenstown, Tiong Bahru
3                         Telok Blangah, Harbourfront
4   Pasir Panjang, Hong Leong Garden, Clementi New...
5                      High Street, Beach Road (part)
6                            Middle Road, Golden Mile
7    Little India, Farrer Park, Jalan Besar, Lavender
8                    Orchard, Cairnhill, River Valley
9         Ardmore, Bukit Timah, Holland Road, Tanglin
10                     Watten Estate, Novena, Thomson
11                    Balestier, Toa Payoh, Serangoon
12                               Macpherson, Braddell
13                                     Geylang, Eunos
14                      Katong, Joo Chiat, Amber Road
15       Bedok, Upper East Coast, Eastwood, Kew Drive
16                                     Loyang, Changi
17                         Simei, Tampines, Pasir Ris
18                 Serangoon Garden, Hougang, Punggol
19                                 Bishan, Ang Mo Kio
20       Upper Bukit Timah, Clementi Park, Ulu Pandan
21                                       Jurong, Tuas
22  Hillview, Dairy Farm, Bukit Panjang, Choa Chu ...
23                               Lim Chu Kang, Tengah
24                       Kranji, Woodgrove, Woodlands
25                          Upper Thomson, Springleaf
26                                  Yishun, Sembawang
27                                            Seletar

There are multiples places in each row. We want each place to occupy a single row. Let's do that.

In [12]:
df1=df1[0].str.split(',',expand=True)
df1

0                   1                   2               3
0       Raffles Place               Cecil              Marina   People's Park
1               Anson       Tanjong Pagar                None            None
2         Bukit Merah          Queenstown         Tiong Bahru            None
3       Telok Blangah        Harbourfront                None            None
4       Pasir Panjang   Hong Leong Garden   Clementi New Town            None
5         High Street   Beach Road (part)                None            None
6         Middle Road         Golden Mile                None            None
7        Little India         Farrer Park         Jalan Besar        Lavender
8             Orchard           Cairnhill        River Valley            None
9             Ardmore         Bukit Timah        Holland Road         Tanglin
10      Watten Estate              Novena             Thomson            None
11          Balestier           Toa Payoh           Serangoon            None
12         Macpherson            Braddell                None            None
13            Geylang               Eunos                None            None
14             Katong           Joo Chiat          Amber Road            None
15              Bedok    Upper East Coast            Eastwood       Kew Drive
16             Loyang              Changi                None            None
17              Simei            Tampines           Pasir Ris            None
18   Serangoon Garden             Hougang             Punggol            None
19             Bishan          Ang Mo Kio                None            None
20  Upper Bukit Timah       Clementi Park          Ulu Pandan            None
21             Jurong                Tuas                None            None
22           Hillview          Dairy Farm       Bukit Panjang   Choa Chu Kang
23       Lim Chu Kang              Tengah                None            None
24             Kranji           Woodgrove           Woodlands            None
25      Upper Thomson          Springleaf                None            None
26             Yishun           Sembawang                None            None
27            Seletar                None                None            None

In [13]:
#Here, we are appending each column of the DataFrame to a list and converting that list back to a DataFrame
oneCol = []
colLength = 4
for k in range(colLength):
    oneCol.append(df1[k])
df2 = pd.concat(oneCol, ignore_index=True)
df2=df2.to_frame(name='Places')
df2

Places
0         Raffles Place
1                 Anson
2           Bukit Merah
3         Telok Blangah
4         Pasir Panjang
5           High Street
6           Middle Road
7          Little India
8               Orchard
9               Ardmore
10        Watten Estate
11            Balestier
12           Macpherson
13              Geylang
14               Katong
15                Bedok
16               Loyang
17                Simei
18     Serangoon Garden
19               Bishan
20    Upper Bukit Timah
21               Jurong
22             Hillview
23         Lim Chu Kang
24               Kranji
25        Upper Thomson
26               Yishun
27              Seletar
28                Cecil
29        Tanjong Pagar
30           Queenstown
31         Harbourfront
32    Hong Leong Garden
33    Beach Road (part)
34          Golden Mile
35          Farrer Park
36            Cairnhill
37          Bukit Timah
38               Novena
39            Toa Payoh
40             Braddell
41                Eunos
42            Joo Chiat
43     Upper East Coast
44               Changi
45             Tampines
46              Hougang
47           Ang Mo Kio
48        Clementi Park
49                 Tuas
50           Dairy Farm
51               Tengah
52            Woodgrove
53           Springleaf
54            Sembawang
55                 None
56               Marina
57                 None
58          Tiong Bahru
59                 None
60    Clementi New Town
61                 None
62                 None
63          Jalan Besar
64         River Valley
65         Holland Road
66              Thomson
67            Serangoon
68                 None
69                 None
70           Amber Road
71             Eastwood
72                 None
73            Pasir Ris
74              Punggol
75                 None
76           Ulu Pandan
77                 None
78        Bukit Panjang
79                 None
80            Woodlands
81                 None
82                 None
83                 None
84        People's Park
85                 None
86                 None
87                 None
88                 None
89                 None
90                 None
91             Lavender
92                 None
93              Tanglin
94                 None
95                 None
96                 None
97                 None
98                 None
99            Kew Drive
100                None
101                None
102                None
103                None
104                None
105                None
106       Choa Chu Kang
107                None
108                None
109                None
110                None
111                None

In [14]:
df2=df2.dropna()

In [15]:
df2

Places
0         Raffles Place
1                 Anson
2           Bukit Merah
3         Telok Blangah
4         Pasir Panjang
5           High Street
6           Middle Road
7          Little India
8               Orchard
9               Ardmore
10        Watten Estate
11            Balestier
12           Macpherson
13              Geylang
14               Katong
15                Bedok
16               Loyang
17                Simei
18     Serangoon Garden
19               Bishan
20    Upper Bukit Timah
21               Jurong
22             Hillview
23         Lim Chu Kang
24               Kranji
25        Upper Thomson
26               Yishun
27              Seletar
28                Cecil
29        Tanjong Pagar
30           Queenstown
31         Harbourfront
32    Hong Leong Garden
33    Beach Road (part)
34          Golden Mile
35          Farrer Park
36            Cairnhill
37          Bukit Timah
38               Novena
39            Toa Payoh
40             Braddell
41                Eunos
42            Joo Chiat
43     Upper East Coast
44               Changi
45             Tampines
46              Hougang
47           Ang Mo Kio
48        Clementi Park
49                 Tuas
50           Dairy Farm
51               Tengah
52            Woodgrove
53           Springleaf
54            Sembawang
56               Marina
58          Tiong Bahru
60    Clementi New Town
63          Jalan Besar
64         River Valley
65         Holland Road
66              Thomson
67            Serangoon
70           Amber Road
71             Eastwood
73            Pasir Ris
74              Punggol
76           Ulu Pandan
78        Bukit Panjang
80            Woodlands
84        People's Park
91             Lavender
93              Tanglin
99            Kew Drive
106       Choa Chu Kang

In [16]:
df2=df2.reset_index(drop=True)
df=df2

In [17]:
print(df)

                Places
0        Raffles Place
1                Anson
2          Bukit Merah
3        Telok Blangah
4        Pasir Panjang
5          High Street
6          Middle Road
7         Little India
8              Orchard
9              Ardmore
10       Watten Estate
11           Balestier
12          Macpherson
13             Geylang
14              Katong
15               Bedok
16              Loyang
17               Simei
18    Serangoon Garden
19              Bishan
20   Upper Bukit Timah
21              Jurong
22            Hillview
23        Lim Chu Kang
24              Kranji
25       Upper Thomson
26              Yishun
27             Seletar
28               Cecil
29       Tanjong Pagar
30          Queenstown
31        Harbourfront
32   Hong Leong Garden
33   Beach Road (part)
34         Golden Mile
35         Farrer Park
36           Cairnhill
37         Bukit Timah
38              Novena
39           Toa Payoh
40            Braddell
41               Eunos
42         

Thus, we have cleaned the data and finally gotten just the location names.

## 3. Find the geographical coordinates

In [18]:
# define a function to get coordinates
def get_latlng(neighborhood):
    # initialize your variable to None
    lat_lng_coords = None
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        g = geocoder.arcgis('{}, Singapore, Singapore'.format(neighborhood))
        lat_lng_coords = g.latlng
    return lat_lng_coords

In [19]:
# call the function to get the coordinates, store in a new list using list comprehension
coords = [ get_latlng(neighborhood) for neighborhood in df["Places"].tolist() ]

In [20]:
coords

[[1.2818900000000326, 103.84912000000008],
 [1.3534439970000562, 103.81650913600004],
 [1.2832199522478398, 103.81675993782109],
 [1.2750900000000343, 103.81980000000004],
 [1.2922900000000368, 103.76819000000006],
 [1.2906179999999985, 103.8494475],
 [1.2994527048926754, 103.8528614919609],
 [1.3110700000000293, 103.85483000000005],
 [1.3011200000000258, 103.83955000000009],
 [1.3094899555660588, 103.82839994113931],
 [1.3286700000000025, 103.80964950000003],
 [1.3263690150486942, 103.84225302758928],
 [1.3278300693923344, 103.88544992281749],
 [1.3114700000000425, 103.88218000000006],
 [1.3045700000000693, 103.90288000000004],
 [1.3242500000000632, 103.95297000000005],
 [1.3749700000000757, 103.97395000000006],
 [1.3429000000000428, 103.95435000000003],
 [1.3640310000000029, 103.86020475000002],
 [1.3507900000000745, 103.85110000000009],
 [1.3640267913153747, 103.76764501565134],
 [1.3208800000000451, 103.74532000000005],
 [1.3621554615653328, 103.76587008156457],
 [1.419670000000053

In [21]:
# create temporary dataframe to populate the coordinates into Latitude and Longitude
df_coords = pd.DataFrame(coords, columns=['Latitude', 'Longitude'])

In [22]:
# merge the coordinates into the original dataframe
df['Latitude'] = df_coords['Latitude']
df['Longitude'] = df_coords['Longitude']

In [23]:
# check the neighborhoods and the coordinates
print(df.shape)
df

(75, 3)


Places  Latitude   Longitude
0        Raffles Place  1.281890  103.849120
1                Anson  1.353444  103.816509
2          Bukit Merah  1.283220  103.816760
3        Telok Blangah  1.275090  103.819800
4        Pasir Panjang  1.292290  103.768190
5          High Street  1.290618  103.849447
6          Middle Road  1.299453  103.852861
7         Little India  1.311070  103.854830
8              Orchard  1.301120  103.839550
9              Ardmore  1.309490  103.828400
10       Watten Estate  1.328670  103.809650
11           Balestier  1.326369  103.842253
12          Macpherson  1.327830  103.885450
13             Geylang  1.311470  103.882180
14              Katong  1.304570  103.902880
15               Bedok  1.324250  103.952970
16              Loyang  1.374970  103.973950
17               Simei  1.342900  103.954350
18    Serangoon Garden  1.364031  103.860205
19              Bishan  1.350790  103.851100
20   Upper Bukit Timah  1.364027  103.767645
21              Jurong  1.320880  103.745320
22            Hillview  1.362155  103.765870
23        Lim Chu Kang  1.419670  103.702320
24              Kranji  1.429110  103.756200
25       Upper Thomson  1.350250  103.835770
26              Yishun  1.436210  103.835820
27             Seletar  1.384029  103.868236
28               Cecil  1.290410  103.852110
29       Tanjong Pagar  1.278890  103.845390
30          Queenstown  1.299660  103.801720
31        Harbourfront  1.265332  103.818864
32   Hong Leong Garden  1.313577  103.757670
33   Beach Road (part)  1.299645  103.859288
34         Golden Mile  1.302320  103.863900
35         Farrer Park  1.312097  103.851272
36           Cairnhill  1.306566  103.839237
37         Bukit Timah  1.340410  103.772210
38              Novena  1.319100  103.843720
39           Toa Payoh  1.334480  103.851080
40            Braddell  1.343310  103.853573
41               Eunos  1.320840  103.899800
42           Joo Chiat  1.312430  103.902409
43    Upper East Coast  1.317867  103.949770
44              Changi  1.369960  103.993110
45            Tampines  1.368190  103.929480
46             Hougang  1.371240  103.891620
47          Ang Mo Kio  1.371610  103.845460
48       Clementi Park  1.327896  103.765208
49                Tuas  1.311820  103.630520
50          Dairy Farm  1.365138  103.768884
51              Tengah  1.382499  103.724822
52           Woodgrove  1.428723  103.781381
53          Springleaf  1.396728  103.821266
54           Sembawang  1.447940  103.818910
55              Marina  1.292270  103.763250
56         Tiong Bahru  1.289530  103.832080
57   Clementi New Town  1.315830  103.764720
58         Jalan Besar  1.307100  103.858420
59        River Valley  1.296855  103.834348
60        Holland Road  1.323301  103.784996
61             Thomson  1.361900  103.839380
62           Serangoon  1.355540  103.876600
63          Amber Road  1.300872  103.901635
64            Eastwood  1.320997  103.957019
65           Pasir Ris  1.371940  103.949940
66             Punggol  1.402460  103.906860
67          Ulu Pandan  1.320603  103.776775
68       Bukit Panjang  1.378770  103.769770
69           Woodlands  1.435850  103.786980
70       People's Park  1.285370  103.843370
71            Lavender  1.360920  103.990060
72             Tanglin  1.299751  103.817357
73           Kew Drive  1.320388  103.950753
74       Choa Chu Kang  1.386160  103.746180

In [24]:
# save the DataFrame as CSV file
df.to_csv("df.csv", index=False)

In [25]:
# get the coordinates of Kuala Lumpur
address = 'Singapore, Singapore'

geolocator = Nominatim(user_agent="my-application")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Singapore is  {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Singapore is  1.357107, 103.8194992.


In [26]:
# create map of Singapore using latitude and longitude values
map_s = folium.Map(location=[latitude, longitude], zoom_start=11)

# add markers to map
for lat, lng, places in zip(df['Latitude'], df['Longitude'], df['Places']):
    label = '{}'.format(places)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7).add_to(map_s)  
    
map_s

In [27]:
# save the map as HTML file
map_s.save('map_s.html')

In [28]:
# define Foursquare Credentials and Version
CLIENT_ID = '2E1YRPNHZ4HCYEISAC1YTL1WNX0Y40SWHQKVMOOSSJKDRK3L' # your Foursquare ID
CLIENT_SECRET = 'LHJUEVEIUTBDECA53UNOTHQOX2EZ4RDNQRSR04SDIXOUCW51' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: 2E1YRPNHZ4HCYEISAC1YTL1WNX0Y40SWHQKVMOOSSJKDRK3L
CLIENT_SECRET:LHJUEVEIUTBDECA53UNOTHQOX2EZ4RDNQRSR04SDIXOUCW51


Explore the first neighbourhood:

In [29]:
place_latitude = df.loc[0, 'Latitude'] 
place_longitude = df.loc[0, 'Longitude'] 

place_name = df.loc[0, 'Places'] 

print('Latitude and longitude values of {} are {}, {}.'.format(place_name, 
                                                               place_latitude, 
                                                               place_longitude))

Latitude and longitude values of Raffles Place are 1.2818900000000326, 103.84912000000008.


In [30]:
limit=100
radius=500
url='https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(CLIENT_ID,CLIENT_SECRET,VERSION,place_latitude,place_longitude,radius,limit)
url

'https://api.foursquare.com/v2/venues/explore?client_id=2E1YRPNHZ4HCYEISAC1YTL1WNX0Y40SWHQKVMOOSSJKDRK3L&client_secret=LHJUEVEIUTBDECA53UNOTHQOX2EZ4RDNQRSR04SDIXOUCW51&v=20180605&ll=1.2818900000000326,103.84912000000008&radius=500&limit=100'

In [31]:
results = requests.get(url).json()
results

{'meta': {'code': 200, 'requestId': '5e3e846f69babe001b078648'},
 'response': {'suggestedFilters': {'header': 'Tap to show:',
   'filters': [{'name': 'Open now', 'key': 'openNow'}]},
  'headerLocation': 'Financial District',
  'headerFullLocation': 'Financial District, Singapore',
  'headerLocationGranularity': 'neighborhood',
  'totalResults': 164,
  'suggestedBounds': {'ne': {'lat': 1.2863900045000372,
    'lng': 103.85361272686984},
   'sw': {'lat': 1.277389995500028, 'lng': 103.84462727313033}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '57831d2b498eb7aacd46454b',
       'name': 'Fat Saigon Boy',
       'location': {'address': '51 Telok Ayer St #01-02',
        'lat': 1.2829771911083339,
        'lng': 103.84906805089604,
        'labeledLatLngs': [{'label': 'di

The result is in a JSON file. Let's convert it to a DataFrame and clean it.

In [32]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [33]:
venues = results['response']['groups'][0]['items']#JSON file
nearby_venues = json_normalize(venues) # flatten JSON
nearby_venues

referralId  reasons.count  \
0    e-0-57831d2b498eb7aacd46454b-0              0   
1    e-0-519d916f498ea9ac42f23088-1              0   
2    e-0-4df741991f6e94c2c77ef6da-2              0   
3    e-0-56e9512acd10cabb2f042d09-3              0   
4    e-0-55dd3b2f498ee2d1c9ec32ec-4              0   
5    e-0-52c54d0411d2a3d73dae49f6-5              0   
6    e-0-566a5a1d498e0e75b36aa41d-6              0   
7    e-0-4f704af9e4b07a4bc6edd2a9-7              0   
8    e-0-4e741c8baeb780be09a0321f-8              0   
9    e-0-4b625e08f964a5208f442ae3-9              0   
10  e-0-4b13fe99f964a520659b23e3-10              0   
11  e-0-5b2b3525cd441c002cfa5f34-11              0   
12  e-0-51b49e49abd88dd0b4e7330f-12              0   
13  e-0-551bd574498e5f30136a811e-13              0   
14  e-0-51279816e4b0e4084477c34d-14              0   
15  e-0-4b476a40f964a5205e3126e3-15              0   
16  e-0-524d61e811d203ac0e258955-16              0   
17  e-0-55ebe939498e79406dbe4ef9-17              0   
18  e-0-559bcec1498ef1434e22b3c6-18              0   
19  e-0-4e5e1aefe4cdfc603ed5c7c3-19              0   
20  e-0-56d3c557cd10357fe7eb429e-20              0   
21  e-0-5a7a977c872f7d3916e199f9-21              0   
22  e-0-57642221498edc75f496b1d7-22              0   
23  e-0-5919373a5315935b271a1f4f-23              0   
24  e-0-55e82fb8498ea305e6c59bda-24              0   
25  e-0-54119564498e4371f8dce458-25              0   
26  e-0-5c37f6231af852002c0e6b03-26              0   
27  e-0-52024a1e498e5896933f505a-27              0   
28  e-0-50ac616ce4b0fbae222802a7-28              0   
29  e-0-557a6b3c498ed9cb15987433-29              0   
30  e-0-51cd1772498e190193a528a8-30              0   
31  e-0-5ba8e7638b98fd002c7c2b1f-31              0   
32  e-0-55a49050498e801fbf03be73-32              0   
33  e-0-543e53f6498e8eacbba09d5e-33              0   
34  e-0-5657c0cd498e5e36dd8dcd9a-34              0   
35  e-0-586a792404aa4f25645e4e4e-35              0   
36  e-0-5bd69fbbe55d8b002ccf6f9f-36              0   
37  e-0-52ccc68f498e5fa860f691ec-37              0   
38  e-0-54e975f6498e0c8bb883ee29-38              0   
39  e-0-4ce5e809d99f721ef9faa073-39              0   
40  e-0-566ea8e6498ee8c21fa57b5b-40              0   
41  e-0-553b2460498e8cfc0a3cdc32-41              0   
42  e-0-5a0a815ab546184394622ff6-42              0   
43  e-0-4fc8aecee4b08eb1f57a1a81-43              0   
44  e-0-4c57877d6201e21e49b7e86e-44              0   
45  e-0-57d2afc0498e99dbb27870da-45              0   
46  e-0-4b05880ef964a520e4ae22e3-46              0   
47  e-0-525699bf498e6701439cb8df-47              0   
48  e-0-53ae48b4498ec970f3cc0455-48              0   
49  e-0-59de3d35c21cb12aaf9ed424-49              0   
50  e-0-56c5ad91cd10c0576881c9f7-50              0   
51  e-0-4f41d3b4e4b005b5362db142-51              0   
52  e-0-59538b0ac824ae5235423946-52              0   
53  e-0-51245408e4b07c9613693ff3-53              0   
54  e-0-50cf13ffe4b0d07034277b23-54              0   
55  e-0-4c3e98640596c92878978478-55              0   
56  e-0-570f1c8f498e7219437034a9-56              0   
57  e-0-582163ff1dbf6c7a757c143c-57              0   
58  e-0-53db460f498e18a343d830db-58              0   
59  e-0-55fe3da6498e0c5eaa442250-59              0   
60  e-0-5a675efbd41bb76f81c836c1-60              0   
61  e-0-4d3913bab5abb1f75c13e498-61              0   
62  e-0-4e3f9e6dfa76455375d3f59f-62              0   
63  e-0-50248ddde4b0bb3db3a6ff8a-63              0   
64  e-0-5ac619818b98fd224e0c295e-64              0   
65  e-0-5bab10b9364d97002cc5e458-65              0   
66  e-0-4c419bceff711b8d2c281205-66              0   
67  e-0-4b0a7b55f964a520552423e3-67              0   
68  e-0-5ad0c2d32b9844361456cb80-68              0   
69  e-0-4b2f5ccef964a520f3ea24e3-69              0   
70  e-0-4ebc743a02d5e32b7b72a3bb-70              0   
71  e-0-4b6a6236f964a5200fd42be3-71              0   
72  e-0-56d81de5498e8c565699d3d6-72              0   
73  e-0-4d08478ec26ba143728f1

Filter out the columns we don't require and extract only the category from venue.categories

In [34]:
# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

name             categories       lat         lng
0                  Fat Saigon Boy  Vietnamese Restaurant  1.282977  103.849068
1                      Amoy Hotel                  Hotel  1.283118  103.848539
2  Luke's Oyster Bar & Chop House     Seafood Restaurant  1.282459  103.847240
3                       Freehouse            Beer Garden  1.281254  103.848513
4                   Grain Traders             Restaurant  1.281468  103.850039

In [35]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

100 venues were returned by Foursquare.


In [36]:
def getNearbyVenues(names, latitudes, longitudes, radius=1000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            limit)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Place', 
                  'Place Latitude', 
                  'Place Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [39]:
singapore_venues = getNearbyVenues(names=df['Places'],
                                   latitudes=df['Latitude'],
                                   longitudes=df['Longitude']
                                  )

Raffles Place
Anson
Bukit Merah
Telok Blangah
Pasir Panjang
High Street
Middle Road
Little India
Orchard
Ardmore
Watten Estate
Balestier
Macpherson
Geylang
Katong
Bedok
Loyang
Simei
Serangoon Garden
Bishan
Upper Bukit Timah
Jurong
Hillview
Lim Chu Kang
Kranji
Upper Thomson
Yishun
Seletar
 Cecil
 Tanjong Pagar
 Queenstown
 Harbourfront
 Hong Leong Garden
 Beach Road (part)
 Golden Mile
 Farrer Park
 Cairnhill
 Bukit Timah
 Novena
 Toa Payoh
 Braddell
 Eunos
 Joo Chiat
 Upper East Coast
 Changi
 Tampines
 Hougang
 Ang Mo Kio
 Clementi Park
 Tuas
 Dairy Farm
 Tengah
 Woodgrove
 Springleaf
 Sembawang
 Marina
 Tiong Bahru
 Clementi New Town
 Jalan Besar
 River Valley
 Holland Road
 Thomson
 Serangoon
 Amber Road
 Eastwood
 Pasir Ris
 Punggol
 Ulu Pandan
 Bukit Panjang
 Woodlands
 People's Park
 Lavender
 Tanglin
 Kew Drive
 Choa Chu Kang


In [40]:
singapore_venues

Place  Place Latitude  Place Longitude  \
0          Raffles Place        1.281890       103.849120   
1          Raffles Place        1.281890       103.849120   
2          Raffles Place        1.281890       103.849120   
3          Raffles Place        1.281890       103.849120   
4          Raffles Place        1.281890       103.849120   
5          Raffles Place        1.281890       103.849120   
6          Raffles Place        1.281890       103.849120   
7          Raffles Place        1.281890       103.849120   
8          Raffles Place        1.281890       103.849120   
9          Raffles Place        1.281890       103.849120   
10         Raffles Place        1.281890       103.849120   
11         Raffles Place        1.281890       103.849120   
12         Raffles Place        1.281890       103.849120   
13         Raffles Place        1.281890       103.849120   
14         Raffles Place        1.281890       103.849120   
15         Raffles Place        1.281890       103.849120   
16         Raffles Place        1.281890       103.849120   
17         Raffles Place        1.281890       103.849120   
18         Raffles Place        1.281890       103.849120   
19         Raffles Place        1.281890       103.849120   
20         Raffles Place        1.281890       103.849120   
21         Raffles Place        1.281890       103.849120   
22         Raffles Place        1.281890       103.849120   
23         Raffles Place        1.281890       103.849120   
24         Raffles Place        1.281890       103.849120   
25         Raffles Place        1.281890       103.849120   
26         Raffles Place        1.281890       103.849120   
27         Raffles Place        1.281890       103.849120   
28         Raffles Place        1.281890       103.849120   
29         Raffles Place        1.281890       103.849120   
30         Raffles Place        1.281890       103.849120   
31         Raffles Place        1.281890       103.849120   
32         Raffles Place        1.281890       103.849120   
33         Raffles Place        1.281890       103.849120   
34         Raffles Place        1.281890       103.849120   
35         Raffles Place        1.281890       103.849120   
36         Raffles Place        1.281890       103.849120   
37         Raffles Place        1.281890       103.849120   
38         Raffles Place        1.281890       103.849120   
39         Raffles Place        1.281890       103.849120   
40         Raffles Place        1.281890       103.849120   
41         Raffles Place        1.281890       103.849120   
42         Raffles Place        1.281890       103.849120   
43         Raffles Place        1.281890       103.849120   
44         Raffles Place        1.281890       103.849120   
45         Raffles Place        1.281890       103.849120   
46         Raffles Place        1.281890       103.849120   
47         Raffles Place        1.281890       103.849120   
48         Raffles Place        1.281890       103.849120   
49         Raffles Place        1.281890       103.849120   
50         Raffles Place        1.281890       103.849120   
51         Raffles Place        1.281890       103.849120   
52         Raffles Place        1.281890       103.849120   
53         Raffles Place        1.281890       103.849120   
54         Raffles Place        1.281890       103.849120   
55         Raffles Place        1.281890       103.849120   
56         Raffles Place        1.281890       103.849120   
57         Raffles Place        1.281890       103.849120   
58         Raffles Place        1.281890       103.849120   
59         Raffles Place        1.281890       103.849120   
60         Raffles Place        1.281890       103.849120   
61         Raffles Place        1.281890       103.849120   
62         Raffles Place        1.281890       103.849120   
63         Raffles Place        1.281890       103.849120   
64         Raffles Place        1.281890       103.849

In [41]:
singapore_venues.to_csv("singapore_venues.csv", index=False)

In [42]:
singapore_venues.shape

(4930, 7)

Finding the number of venues returned for each place

In [46]:
singapore_venues.groupby(["Place"]).count()

Place Latitude  Place Longitude  Venue  Venue Latitude  \
Place                                                                        
 Amber Road                    100              100    100             100   
 Ang Mo Kio                     79               79     79              79   
 Beach Road (part)             100              100    100             100   
 Braddell                      100              100    100             100   
 Bukit Panjang                  60               60     60              60   
 Bukit Timah                    85               85     85              85   
 Cairnhill                     100              100    100             100   
 Cecil                         100              100    100             100   
 Changi                         57               57     57              57   
 Choa Chu Kang                  37               37     37              37   
 Clementi New Town              91               91     91              91   
 Clementi Park                  27               27     27              27   
 Dairy Farm                     36               36     36              36   
 Eastwood                       37               37     37              37   
 Eunos                         100              100    100             100   
 Farrer Park                   100              100    100             100   
 Golden Mile                   100              100    100             100   
 Harbourfront                  100              100    100             100   
 Holland Road                   22               22     22              22   
 Hong Leong Garden              91               91     91              91   
 Hougang                        68               68     68              68   
 Jalan Besar                   100              100    100             100   
 Joo Chiat                     100              100    100             100   
 Kew Drive                      36               36     36              36   
 Lavender                       65               65     65              65   
 Marina                         14               14     14              14   
 Novena                        100              100    100             100   
 Pasir Ris                      35               35     35              35   
 People's Park                 100              100    100             100   
 Punggol                        62               62     62              62   
 Queenstown                     56               56     56              56   
 River Valley                  100              100    100             100   
 Sembawang                      50               50     50              50   
 Serangoon                      75               75     75              75   
 Springleaf                     27               27     27              27   
 Tampines                       28               28     28              28   
 Tanglin                        72               72     72              72   
 Tanjong Pagar                 100              100    100             100   
 Tengah                         17               17     17              17   
 Thomson                        47               47     47              47   
 Tiong Bahru                   100              100    100             100   
 Toa Payoh                     100              100    100             100   
 Tuas                            8                8      8               8   
 Ulu Pandan                     30               30     30              30   
 Upper East Coast               16               16     16              16   
 Woodgrove                      58               58     58              58   
 Woodlands                      81               81     81              81   
Anson                           14               14     14              14   
Ardmore                        100              100    100             100   
Balestier                      100        

In [49]:
print('There are {} unique categories.'.format(len(singapore_venues['Venue Category'].unique())))

There are 324 unique categories.


In [52]:
# print out the list of categories
singapore_venues['Venue Category'].unique()[:324]

array(['Vietnamese Restaurant', 'Hotel', 'Wine Bar', 'Seafood Restaurant',
       'Beer Garden', 'Street Food Gathering', 'Restaurant',
       'Modern European Restaurant', 'Food Court', 'Sandwich Place',
       'Martial Arts Dojo', 'Korean Restaurant', 'Bar', 'Café',
       'Japanese Restaurant', 'Mediterranean Restaurant',
       'Italian Restaurant', 'Deli / Bodega', 'Cocktail Bar',
       'Dumpling Restaurant', 'Hotpot Restaurant', 'French Restaurant',
       'Gym / Fitness Center', 'Speakeasy', 'Comfort Food Restaurant',
       'Indian Restaurant', 'Coffee Shop', 'Argentinian Restaurant',
       'Gym', 'Chinese Restaurant', 'Asian Restaurant',
       'Southern / Soul Food Restaurant', 'Burrito Place', 'Salad Place',
       'Lounge', 'Other Great Outdoors', 'Buddhist Temple', 'Bakery',
       'Hostel', 'Spanish Restaurant', 'Pub', 'Peking Duck Restaurant',
       'Hotel Bar', 'Pool', 'Massage Studio', 'Yoga Studio', 'Beer Bar',
       'Waterfront', 'Soup Place', 'Brewery', 'Plaza',

Let's check if one of these categories is shopping mall

In [59]:
singapore_venues[singapore_venues['Venue Category'].str.contains(r"\bshopping\b", case=False)]

Place  Place Latitude  Place Longitude  \
294          High Street        1.290618       103.849447   
310          High Street        1.290618       103.849447   
379          High Street        1.290618       103.849447   
413          Middle Road        1.299453       103.852861   
457          Middle Road        1.299453       103.852861   
601              Orchard        1.301120       103.839550   
611              Orchard        1.301120       103.839550   
628              Orchard        1.301120       103.839550   
638              Orchard        1.301120       103.839550   
642              Orchard        1.301120       103.839550   
672              Orchard        1.301120       103.839550   
732              Ardmore        1.309490       103.828400   
797        Watten Estate        1.328670       103.809650   
847        Watten Estate        1.328670       103.809650   
853        Watten Estate        1.328670       103.809650   
855        Watten Estate        1.328670       103.809650   
933            Balestier        1.326369       103.842253   
1007          Macpherson        1.327830       103.885450   
1042          Macpherson        1.327830       103.885450   
1192              Katong        1.304570       103.902880   
1299               Simei        1.342900       103.954350   
1375    Serangoon Garden        1.364031       103.860205   
1423              Bishan        1.350790       103.851100   
1482   Upper Bukit Timah        1.364027       103.767645   
1485   Upper Bukit Timah        1.364027       103.767645   
1546            Hillview        1.362155       103.765870   
1549            Hillview        1.362155       103.765870   
1644       Upper Thomson        1.350250       103.835770   
1709              Yishun        1.436210       103.835820   
1716              Yishun        1.436210       103.835820   
1757             Seletar        1.384029       103.868236   
1771               Cecil        1.290410       103.852110   
1815               Cecil        1.290410       103.852110   
1850               Cecil        1.290410       103.852110   
1851               Cecil        1.290410       103.852110   
2019        Harbourfront        1.265332       103.818864   
2084        Harbourfront        1.265332       103.818864   
2088        Harbourfront        1.265332       103.818864   
2164   Hong Leong Garden        1.313577       103.757670   
2187   Hong Leong Garden        1.313577       103.757670   
2243   Beach Road (part)        1.299645       103.859288   
2265   Beach Road (part)        1.299645       103.859288   
2286   Beach Road (part)        1.299645       103.859288   
2388         Golden Mile        1.302320       103.863900   
2512           Cairnhill        1.306566       103.839237   
2529           Cairnhill        1.306566       103.839237   
2547           Cairnhill        1.306566       103.839237   
2571           Cairnhill        1.306566       103.839237   
2594           Cairnhill        1.306566       103.839237   
2608           Cairnhill        1.306566       103.839237   
2790              Novena        1.319100       103.843720   
2942            Braddell        1.343310       103.853573   
3044               Eunos        1.320840       103.899800   
3090               Eunos        1.320840       103.899800   
3094               Eunos        1.320840       103.899800   
3194           Joo Chiat        1.312430       103.902409   
3334             Hougang        1.371240       103.891620   
3342             Hougang        1.371240       103.891620   
3401          Ang Mo Kio        1.371610       103.845460   
3492          Dairy Farm        1.365138       103.768884   
3494          Dairy Farm        1.365138       103.768884   
3535           Woodgrove        1.428723       103.781381   
3554           Woodgrove        1.428723       103.781381   
3567           Woodgrove        1.428723       103.781381   
3576           Woodgrove        1.428723       103.781

In [78]:
singapore_venues[singapore_venues['Venue Category'].str.contains(r"\bplaza\b", case=False)]

Place  Place Latitude  Place Longitude  \
85       Raffles Place        1.281890       103.849120   
288      Pasir Panjang        1.292290       103.768190   
338        High Street        1.290618       103.849447   
375        High Street        1.290618       103.849447   
422        Middle Road        1.299453       103.852861   
1367  Serangoon Garden        1.364031       103.860205   
1802             Cecil        1.290410       103.852110   
1804             Cecil        1.290410       103.852110   
2025      Harbourfront        1.265332       103.818864   
3742       Tiong Bahru        1.289530       103.832080   
4446           Punggol        1.402460       103.906860   
4528     Bukit Panjang        1.378770       103.769770   
4611         Woodlands        1.435850       103.786980   
4686     People's Park        1.285370       103.843370   

                                Venue  Venue Latitude  Venue Longitude  \
85                        Asia Square        1.278340       103.851513   
288       The Stage @ West Coast Park        1.297106       103.761759   
338                 Chijmes (CHIJMES)        1.295070       103.852128   
375                     One Fullerton        1.285797       103.854181   
422                 Chijmes (CHIJMES)        1.295070       103.852128   
1367          Serangoon Garden Circus        1.364061       103.865816   
1802                Chijmes (CHIJMES)        1.295070       103.852128   
1804                    One Fullerton        1.285797       103.854181   
2025  Vivocity Outdoor Water Fountain        1.265170       103.821764   
3742                   Robertson Quay        1.290924       103.840774   
4446                  Community Plaza        1.401762       103.914657   
4528           Hillion Mall MRT Plaza        1.378080       103.762616   
4611                        883 Plaza        1.442565       103.790936   
4686                   Robertson Quay        1.290924       103.840774   

        Venue Category  
85               Plaza  
288              Plaza  
338              Plaza  
375              Plaza  
422              Plaza  
1367             Plaza  
1802             Plaza  
1804             Plaza  
2025             Plaza  
3742  Pedestrian Plaza  
4446             Plaza  
4528  Pedestrian Plaza  
4611             Plaza  
4686  Pedestrian Plaza

In [79]:
singapore_venues['Venue Category'] = singapore_venues['Venue Category'].str.replace('Shopping Plaza','Shopping Mall')
singapore_venues['Venue Category'] = singapore_venues['Venue Category'].str.replace('Plaza','Shopping Mall')
singapore_venues['Venue Category'] = singapore_venues['Venue Category'].str.replace('Pedestrian Plaza','Shopping Mall')

In [80]:
singapore_venues[singapore_venues['Venue Category'].str.contains(r"\bshopping\b", case=False)]

Place  Place Latitude  Place Longitude  \
85         Raffles Place        1.281890       103.849120   
288        Pasir Panjang        1.292290       103.768190   
294          High Street        1.290618       103.849447   
310          High Street        1.290618       103.849447   
338          High Street        1.290618       103.849447   
375          High Street        1.290618       103.849447   
379          High Street        1.290618       103.849447   
413          Middle Road        1.299453       103.852861   
422          Middle Road        1.299453       103.852861   
457          Middle Road        1.299453       103.852861   
601              Orchard        1.301120       103.839550   
611              Orchard        1.301120       103.839550   
628              Orchard        1.301120       103.839550   
638              Orchard        1.301120       103.839550   
642              Orchard        1.301120       103.839550   
672              Orchard        1.301120       103.839550   
732              Ardmore        1.309490       103.828400   
797        Watten Estate        1.328670       103.809650   
847        Watten Estate        1.328670       103.809650   
853        Watten Estate        1.328670       103.809650   
855        Watten Estate        1.328670       103.809650   
933            Balestier        1.326369       103.842253   
1007          Macpherson        1.327830       103.885450   
1042          Macpherson        1.327830       103.885450   
1192              Katong        1.304570       103.902880   
1299               Simei        1.342900       103.954350   
1367    Serangoon Garden        1.364031       103.860205   
1375    Serangoon Garden        1.364031       103.860205   
1423              Bishan        1.350790       103.851100   
1482   Upper Bukit Timah        1.364027       103.767645   
1485   Upper Bukit Timah        1.364027       103.767645   
1546            Hillview        1.362155       103.765870   
1549            Hillview        1.362155       103.765870   
1644       Upper Thomson        1.350250       103.835770   
1709              Yishun        1.436210       103.835820   
1716              Yishun        1.436210       103.835820   
1757             Seletar        1.384029       103.868236   
1771               Cecil        1.290410       103.852110   
1802               Cecil        1.290410       103.852110   
1804               Cecil        1.290410       103.852110   
1815               Cecil        1.290410       103.852110   
1850               Cecil        1.290410       103.852110   
1851               Cecil        1.290410       103.852110   
2019        Harbourfront        1.265332       103.818864   
2025        Harbourfront        1.265332       103.818864   
2084        Harbourfront        1.265332       103.818864   
2088        Harbourfront        1.265332       103.818864   
2164   Hong Leong Garden        1.313577       103.757670   
2187   Hong Leong Garden        1.313577       103.757670   
2243   Beach Road (part)        1.299645       103.859288   
2265   Beach Road (part)        1.299645       103.859288   
2286   Beach Road (part)        1.299645       103.859288   
2388         Golden Mile        1.302320       103.863900   
2512           Cairnhill        1.306566       103.839237   
2529           Cairnhill        1.306566       103.839237   
2547           Cairnhill        1.306566       103.839237   
2571           Cairnhill        1.306566       103.839237   
2594           Cairnhill        1.306566       103.839237   
2608           Cairnhill        1.306566       103.839237   
2790              Novena        1.319100       103.843720   
2942            Braddell        1.343310       103.853573   
3044               Eunos        1.320840       103.899800   
3090               Eunos        1.320840       103.899800   
3094               Eunos        1.320840       103.899800   
3194           Joo Chiat        1.312430       103.902

In [81]:
# one hot encoding
s_onehot = pd.get_dummies(singapore_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
s_onehot['Place'] = singapore_venues['Place'] 

# move neighborhood column to the first column
fixed_columns = [s_onehot.columns[-1]] + list(s_onehot.columns[:-1])
s_onehot = s_onehot[fixed_columns]

print(s_onehot.shape)
s_onehot.head()

(4930, 323)


Place  ATM  Accessories Store  Airport  Airport Food Court  \
0  Raffles Place    0                  0        0                   0   
1  Raffles Place    0                  0        0                   0   
2  Raffles Place    0                  0        0                   0   
3  Raffles Place    0                  0        0                   0   
4  Raffles Place    0                  0        0                   0   

   Airport Gate  Airport Lounge  Airport Terminal  American Restaurant  \
0             0               0                 0                    0   
1             0               0                 0                    0   
2             0               0                 0                    0   
3             0               0                 0                    0   
4             0               0                 0                    0   

   Aquarium  Arcade  Argentinian Restaurant  Art Gallery  Art Museum  \
0         0       0                       0            0           0   
1         0       0                       0            0           0   
2         0       0                       0            0           0   
3         0       0                       0            0           0   
4         0       0                       0            0           0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0                    0                     0                 0   
1                    0                     0                 0   
2                    0                     0                 0   
3                    0                     0                 0   
4                    0                     0                 0   

   Athletics & Sports  Australian Restaurant  Auto Workshop  Automotive Shop  \
0                   0                      0              0                0   
1                   0                      0              0                0   
2                   0                      0              0                0   
3                   0                      0              0                0   
4                   0                      0              0                0   

   BBQ Joint  Baby Store  Bagel Shop  Bakery  Bank  Bar  Baseball Stadium  \
0          0           0           0       0     0    0                 0   
1          0           0           0       0     0    0                 0   
2          0           0           0       0     0    0                 0   
3          0           0           0       0     0    0                 0   
4          0           0           0       0     0    0                 0   

   Basketball Court  Basketball Stadium  Beach  Bed & Breakfast  Beer Bar  \
0                 0                   0      0                0         0   
1                 0                   0      0                0         0   
2                 0                   0      0                0         0   
3                 0                   0      0                0         0   
4                 0                   0      0                0         0   

   Beer Garden  Beer Store  Belgian Restaurant  Betting Shop  \
0            0           0                   0             0   
1            0           0                   0             0   
2            0           0                   0             0   
3            0           0                   0             0   
4            1           0                   0             0   

   Bike Rental / Bike Share  Bike Trail  Bistro  Board Shop  Boarding House  \
0                         0           0       0           0               0   
1                         0           0       0           0               0   
2                         0           0       0           0               0   
3                         0           0       0           0               0   
4                         0           0       0           0               0   

   Bookstore  Border Crossing 

In [82]:
s_grouped = s_onehot.groupby(["Place"]).mean().reset_index()

print(s_grouped.shape)
s_grouped

(75, 323)


Place       ATM  Accessories Store   Airport  \
0           Amber Road  0.000000           0.000000  0.000000   
1           Ang Mo Kio  0.000000           0.000000  0.000000   
2    Beach Road (part)  0.000000           0.000000  0.000000   
3             Braddell  0.000000           0.000000  0.000000   
4        Bukit Panjang  0.000000           0.000000  0.000000   
5          Bukit Timah  0.000000           0.000000  0.000000   
6            Cairnhill  0.000000           0.000000  0.000000   
7                Cecil  0.000000           0.000000  0.000000   
8               Changi  0.000000           0.000000  0.035088   
9        Choa Chu Kang  0.000000           0.000000  0.000000   
10   Clementi New Town  0.010989           0.000000  0.000000   
11       Clementi Park  0.000000           0.000000  0.000000   
12          Dairy Farm  0.000000           0.000000  0.000000   
13            Eastwood  0.000000           0.000000  0.000000   
14               Eunos  0.000000           0.000000  0.000000   
15         Farrer Park  0.000000           0.000000  0.000000   
16         Golden Mile  0.000000           0.000000  0.000000   
17        Harbourfront  0.000000           0.000000  0.000000   
18        Holland Road  0.000000           0.000000  0.000000   
19   Hong Leong Garden  0.010989           0.000000  0.000000   
20             Hougang  0.000000           0.000000  0.000000   
21         Jalan Besar  0.000000           0.000000  0.000000   
22           Joo Chiat  0.000000           0.000000  0.000000   
23           Kew Drive  0.000000           0.000000  0.000000   
24            Lavender  0.000000           0.015385  0.046154   
25              Marina  0.000000           0.000000  0.000000   
26              Novena  0.000000           0.000000  0.000000   
27           Pasir Ris  0.000000           0.000000  0.000000   
28       People's Park  0.000000           0.000000  0.000000   
29             Punggol  0.000000           0.000000  0.000000   
30          Queenstown  0.000000           0.000000  0.000000   
31        River Valley  0.000000           0.000000  0.000000   
32           Sembawang  0.000000           0.000000  0.000000   
33           Serangoon  0.000000           0.000000  0.000000   
34          Springleaf  0.000000           0.000000  0.000000   
35            Tampines  0.000000           0.000000  0.000000   
36             Tanglin  0.000000           0.000000  0.000000   
37       Tanjong Pagar  0.000000           0.000000  0.000000   
38              Tengah  0.000000           0.000000  0.000000   
39             Thomson  0.000000           0.000000  0.000000   
40         Tiong Bahru  0.000000           0.000000  0.000000   
41           Toa Payoh  0.000000           0.000000  0.000000   
42                Tuas  0.000000           0.000000  0.000000   
43          Ulu Pandan  0.000000           0.000000  0.000000   
44    Upper East Coast  0.000000           0.000000  0.000000   
45           Woodgrove  0.000000           0.000000  0.000000   
46           Woodlands  0.000000           0.000000  0.000000   
47               Anson  0.000000           0.000000  0.000000   
48             Ardmore  0.000000           0.000000  0.000000   
49           Balestier  0.000000           0.000000  0.000000   
50               Bedok  0.000000           0.000000  0.000000   
51              Bishan  0.000000           0.000000  0.000000   
52         Bukit Merah  0.000000           0.000000  0.000000   
53             Geylang  0.000000           0.000000  0.000000   
54         High Street  0.000000           0.000000  0.000000   
55            Hillview  0.000000           0.000000  0.000000   
56              Jurong  0.000000           0.000000  0.000000   
57              Katong  0.000000           0.000000  0.000000   
58              Kranji  0.000000           0.000000  0.000000   
59        Lim Chu Kang  0.000000           0.000000  0.000000   
60        Little India  0.000000           0.000000 

In [83]:
s_mall = s_grouped[["Place","Shopping Mall"]]

In [84]:
s_mall

Place  Shopping Mall
0           Amber Road       0.020000
1           Ang Mo Kio       0.012658
2    Beach Road (part)       0.030000
3             Braddell       0.010000
4        Bukit Panjang       0.033333
5          Bukit Timah       0.000000
6            Cairnhill       0.060000
7                Cecil       0.060000
8               Changi       0.000000
9        Choa Chu Kang       0.027027
10   Clementi New Town       0.010989
11       Clementi Park       0.000000
12          Dairy Farm       0.055556
13            Eastwood       0.000000
14               Eunos       0.030000
15         Farrer Park       0.000000
16         Golden Mile       0.010000
17        Harbourfront       0.040000
18        Holland Road       0.045455
19   Hong Leong Garden       0.021978
20             Hougang       0.029412
21         Jalan Besar       0.000000
22           Joo Chiat       0.010000
23           Kew Drive       0.000000
24            Lavender       0.015385
25              Marina       0.000000
26              Novena       0.010000
27           Pasir Ris       0.028571
28       People's Park       0.010000
29             Punggol       0.032258
30          Queenstown       0.000000
31        River Valley       0.080000
32           Sembawang       0.020000
33           Serangoon       0.013333
34          Springleaf       0.000000
35            Tampines       0.000000
36             Tanglin       0.013889
37       Tanjong Pagar       0.000000
38              Tengah       0.000000
39             Thomson       0.000000
40         Tiong Bahru       0.010000
41           Toa Payoh       0.000000
42                Tuas       0.000000
43          Ulu Pandan       0.000000
44    Upper East Coast       0.000000
45           Woodgrove       0.068966
46           Woodlands       0.074074
47               Anson       0.000000
48             Ardmore       0.010000
49           Balestier       0.010000
50               Bedok       0.000000
51              Bishan       0.014706
52         Bukit Merah       0.000000
53             Geylang       0.000000
54         High Street       0.050000
55            Hillview       0.051282
56              Jurong       0.000000
57              Katong       0.010000
58              Kranji       0.000000
59        Lim Chu Kang       0.000000
60        Little India       0.000000
61              Loyang       0.000000
62          Macpherson       0.025316
63         Middle Road       0.030000
64             Orchard       0.060000
65       Pasir Panjang       0.033333
66       Raffles Place       0.010000
67             Seletar       0.071429
68    Serangoon Garden       0.029851
69               Simei       0.022727
70       Telok Blangah       0.000000
71   Upper Bukit Timah       0.054054
72       Upper Thomson       0.012987
73       Watten Estate       0.052632
74              Yishun       0.025000

In [85]:
# set number of clusters
kclusters = 3

s_clustering = s_mall.drop(["Place"], 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(s_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([2, 0, 2, 0, 2, 0, 1, 1, 0, 2], dtype=int32)

In [86]:
# create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.
s_merged = s_mall.copy()

# add clustering labels
s_merged["Cluster Labels"] = kmeans.labels_

In [87]:
s_merged

Place  Shopping Mall  Cluster Labels
0           Amber Road       0.020000               2
1           Ang Mo Kio       0.012658               0
2    Beach Road (part)       0.030000               2
3             Braddell       0.010000               0
4        Bukit Panjang       0.033333               2
5          Bukit Timah       0.000000               0
6            Cairnhill       0.060000               1
7                Cecil       0.060000               1
8               Changi       0.000000               0
9        Choa Chu Kang       0.027027               2
10   Clementi New Town       0.010989               0
11       Clementi Park       0.000000               0
12          Dairy Farm       0.055556               1
13            Eastwood       0.000000               0
14               Eunos       0.030000               2
15         Farrer Park       0.000000               0
16         Golden Mile       0.010000               0
17        Harbourfront       0.040000               2
18        Holland Road       0.045455               1
19   Hong Leong Garden       0.021978               2
20             Hougang       0.029412               2
21         Jalan Besar       0.000000               0
22           Joo Chiat       0.010000               0
23           Kew Drive       0.000000               0
24            Lavender       0.015385               0
25              Marina       0.000000               0
26              Novena       0.010000               0
27           Pasir Ris       0.028571               2
28       People's Park       0.010000               0
29             Punggol       0.032258               2
30          Queenstown       0.000000               0
31        River Valley       0.080000               1
32           Sembawang       0.020000               2
33           Serangoon       0.013333               0
34          Springleaf       0.000000               0
35            Tampines       0.000000               0
36             Tanglin       0.013889               0
37       Tanjong Pagar       0.000000               0
38              Tengah       0.000000               0
39             Thomson       0.000000               0
40         Tiong Bahru       0.010000               0
41           Toa Payoh       0.000000               0
42                Tuas       0.000000               0
43          Ulu Pandan       0.000000               0
44    Upper East Coast       0.000000               0
45           Woodgrove       0.068966               1
46           Woodlands       0.074074               1
47               Anson       0.000000               0
48             Ardmore       0.010000               0
49           Balestier       0.010000               0
50               Bedok       0.000000               0
51              Bishan       0.014706               0
52         Bukit Merah       0.000000               0
53             Geylang       0.000000               0
54         High Street       0.050000               1
55            Hillview       0.051282               1
56              Jurong       0.000000               0
57              Katong       0.010000               0
58              Kranji       0.000000               0
59        Lim Chu Kang       0.000000               0
60        Little India       0.000000               0
61              Loyang       0.000000               0
62          Macpherson       0.025316               2
63         Middle Road       0.030000               2
64             Orchard       0.060000               1
65       Pasir Panjang       0.033333               2
66       Raffles Place       0.010000               0
67             Seletar       0.071429               1
68    Serangoon Garden       0.029851               2
69               Simei       0.022727               2
70       Telok Blangah       0.000000               0
71   Upper Bukit Timah       0.054054               1
72       Upper Thomson       0.012987               0
73       Watten Estat

In [88]:
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
s_merged = s_merged.join(df.set_index("Places"), on="Place")

print(s_merged.shape)
s_merged.head() # check the last columns!

(75, 5)


Place  Shopping Mall  Cluster Labels  Latitude   Longitude
0          Amber Road       0.020000               2  1.300872  103.901635
1          Ang Mo Kio       0.012658               0  1.371610  103.845460
2   Beach Road (part)       0.030000               2  1.299645  103.859288
3            Braddell       0.010000               0  1.343310  103.853573
4       Bukit Panjang       0.033333               2  1.378770  103.769770

In [89]:
s_merged.tail()

Place  Shopping Mall  Cluster Labels  Latitude   Longitude
70      Telok Blangah       0.000000               0  1.275090  103.819800
71  Upper Bukit Timah       0.054054               1  1.364027  103.767645
72      Upper Thomson       0.012987               0  1.350250  103.835770
73      Watten Estate       0.052632               1  1.328670  103.809650
74             Yishun       0.025000               2  1.436210  103.835820

In [90]:
# sort the results by Cluster Labels
print(s_merged.shape)
s_merged.sort_values(["Cluster Labels"], inplace=True)
s_merged

(75, 5)


Place  Shopping Mall  Cluster Labels  Latitude   Longitude
37       Tanjong Pagar       0.000000               0  1.278890  103.845390
60        Little India       0.000000               0  1.311070  103.854830
33           Serangoon       0.013333               0  1.355540  103.876600
34          Springleaf       0.000000               0  1.396728  103.821266
35            Tampines       0.000000               0  1.368190  103.929480
36             Tanglin       0.013889               0  1.299751  103.817357
38              Tengah       0.000000               0  1.382499  103.724822
39             Thomson       0.000000               0  1.361900  103.839380
40         Tiong Bahru       0.010000               0  1.289530  103.832080
41           Toa Payoh       0.000000               0  1.334480  103.851080
42                Tuas       0.000000               0  1.311820  103.630520
43          Ulu Pandan       0.000000               0  1.320603  103.776775
44    Upper East Coast       0.000000               0  1.317867  103.949770
47               Anson       0.000000               0  1.353444  103.816509
48             Ardmore       0.010000               0  1.309490  103.828400
49           Balestier       0.010000               0  1.326369  103.842253
50               Bedok       0.000000               0  1.324250  103.952970
51              Bishan       0.014706               0  1.350790  103.851100
52         Bukit Merah       0.000000               0  1.283220  103.816760
53             Geylang       0.000000               0  1.311470  103.882180
56              Jurong       0.000000               0  1.320880  103.745320
57              Katong       0.010000               0  1.304570  103.902880
58              Kranji       0.000000               0  1.429110  103.756200
59        Lim Chu Kang       0.000000               0  1.419670  103.702320
28       People's Park       0.010000               0  1.285370  103.843370
26              Novena       0.010000               0  1.319100  103.843720
30          Queenstown       0.000000               0  1.299660  103.801720
61              Loyang       0.000000               0  1.374970  103.973950
11       Clementi Park       0.000000               0  1.327896  103.765208
8               Changi       0.000000               0  1.369960  103.993110
25              Marina       0.000000               0  1.292270  103.763250
13            Eastwood       0.000000               0  1.320997  103.957019
15         Farrer Park       0.000000               0  1.312097  103.851272
16         Golden Mile       0.010000               0  1.302320  103.863900
5          Bukit Timah       0.000000               0  1.340410  103.772210
10   Clementi New Town       0.010989               0  1.315830  103.764720
70       Telok Blangah       0.000000               0  1.275090  103.819800
66       Raffles Place       0.010000               0  1.281890  103.849120
21         Jalan Besar       0.000000               0  1.307100  103.858420
22           Joo Chiat       0.010000               0  1.312430  103.902409
3             Braddell       0.010000               0  1.343310  103.853573
72       Upper Thomson       0.012987               0  1.350250  103.835770
23           Kew Drive       0.000000               0  1.320388  103.950753
1           Ang Mo Kio       0.012658               0  1.371610  103.845460
24            Lavender       0.015385               0  1.360920  103.990060
55            Hillview       0.051282               1  1.362155  103.765870
6            Cairnhill       0.060000               1  1.306566  103.839237
7                Cecil       0.060000               1  1.290410  103.852110
71   Upper Bukit Timah       0.054054               1  1.364027  103.767645
54         High Street       0.050000               1  1.290618  103.849447
12          Dairy Farm       0.055556               1  1.365138  103.768884
45           Woodgrove       0.068966               1  1.428723  

In [91]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i+x+(i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(s_merged['Latitude'], s_merged['Longitude'], s_merged['Place'], s_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' - Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

In [92]:
# save the map as HTML file
map_clusters.save('map_clusters.html')

In [93]:
s_merged.loc[s_merged['Cluster Labels'] == 0]

Place  Shopping Mall  Cluster Labels  Latitude   Longitude
37       Tanjong Pagar       0.000000               0  1.278890  103.845390
60        Little India       0.000000               0  1.311070  103.854830
33           Serangoon       0.013333               0  1.355540  103.876600
34          Springleaf       0.000000               0  1.396728  103.821266
35            Tampines       0.000000               0  1.368190  103.929480
36             Tanglin       0.013889               0  1.299751  103.817357
38              Tengah       0.000000               0  1.382499  103.724822
39             Thomson       0.000000               0  1.361900  103.839380
40         Tiong Bahru       0.010000               0  1.289530  103.832080
41           Toa Payoh       0.000000               0  1.334480  103.851080
42                Tuas       0.000000               0  1.311820  103.630520
43          Ulu Pandan       0.000000               0  1.320603  103.776775
44    Upper East Coast       0.000000               0  1.317867  103.949770
47               Anson       0.000000               0  1.353444  103.816509
48             Ardmore       0.010000               0  1.309490  103.828400
49           Balestier       0.010000               0  1.326369  103.842253
50               Bedok       0.000000               0  1.324250  103.952970
51              Bishan       0.014706               0  1.350790  103.851100
52         Bukit Merah       0.000000               0  1.283220  103.816760
53             Geylang       0.000000               0  1.311470  103.882180
56              Jurong       0.000000               0  1.320880  103.745320
57              Katong       0.010000               0  1.304570  103.902880
58              Kranji       0.000000               0  1.429110  103.756200
59        Lim Chu Kang       0.000000               0  1.419670  103.702320
28       People's Park       0.010000               0  1.285370  103.843370
26              Novena       0.010000               0  1.319100  103.843720
30          Queenstown       0.000000               0  1.299660  103.801720
61              Loyang       0.000000               0  1.374970  103.973950
11       Clementi Park       0.000000               0  1.327896  103.765208
8               Changi       0.000000               0  1.369960  103.993110
25              Marina       0.000000               0  1.292270  103.763250
13            Eastwood       0.000000               0  1.320997  103.957019
15         Farrer Park       0.000000               0  1.312097  103.851272
16         Golden Mile       0.010000               0  1.302320  103.863900
5          Bukit Timah       0.000000               0  1.340410  103.772210
10   Clementi New Town       0.010989               0  1.315830  103.764720
70       Telok Blangah       0.000000               0  1.275090  103.819800
66       Raffles Place       0.010000               0  1.281890  103.849120
21         Jalan Besar       0.000000               0  1.307100  103.858420
22           Joo Chiat       0.010000               0  1.312430  103.902409
3             Braddell       0.010000               0  1.343310  103.853573
72       Upper Thomson       0.012987               0  1.350250  103.835770
23           Kew Drive       0.000000               0  1.320388  103.950753
1           Ang Mo Kio       0.012658               0  1.371610  103.845460
24            Lavender       0.015385               0  1.360920  103.990060

In [94]:
s_merged.loc[s_merged['Cluster Labels'] == 1]

Place  Shopping Mall  Cluster Labels  Latitude   Longitude
55           Hillview       0.051282               1  1.362155  103.765870
6           Cairnhill       0.060000               1  1.306566  103.839237
7               Cecil       0.060000               1  1.290410  103.852110
71  Upper Bukit Timah       0.054054               1  1.364027  103.767645
54        High Street       0.050000               1  1.290618  103.849447
12         Dairy Farm       0.055556               1  1.365138  103.768884
45          Woodgrove       0.068966               1  1.428723  103.781381
18       Holland Road       0.045455               1  1.323301  103.784996
73      Watten Estate       0.052632               1  1.328670  103.809650
67            Seletar       0.071429               1  1.384029  103.868236
31       River Valley       0.080000               1  1.296855  103.834348
64            Orchard       0.060000               1  1.301120  103.839550
46          Woodlands       0.074074               1  1.435850  103.786980

In [95]:
s_merged.loc[s_merged['Cluster Labels'] == 2]

Place  Shopping Mall  Cluster Labels  Latitude   Longitude
69               Simei       0.022727               2  1.342900  103.954350
68    Serangoon Garden       0.029851               2  1.364031  103.860205
63         Middle Road       0.030000               2  1.299453  103.852861
65       Pasir Panjang       0.033333               2  1.292290  103.768190
0           Amber Road       0.020000               2  1.300872  103.901635
32           Sembawang       0.020000               2  1.447940  103.818910
29             Punggol       0.032258               2  1.402460  103.906860
27           Pasir Ris       0.028571               2  1.371940  103.949940
20             Hougang       0.029412               2  1.371240  103.891620
19   Hong Leong Garden       0.021978               2  1.313577  103.757670
17        Harbourfront       0.040000               2  1.265332  103.818864
14               Eunos       0.030000               2  1.320840  103.899800
9        Choa Chu Kang       0.027027               2  1.386160  103.746180
4        Bukit Panjang       0.033333               2  1.378770  103.769770
2    Beach Road (part)       0.030000               2  1.299645  103.859288
62          Macpherson       0.025316               2  1.327830  103.885450
74              Yishun       0.025000               2  1.436210  103.835820

Observations:
There seems to be no particular pattern to the way malls are located in Singapore. This points to the fact that each neighbourhood in Singapore is built to be self-sufficient, with most of the facilties available within the neighbourhood. This can be seen from the "singapore_venues" DataFrame as well.

Cluster 1 has the greatest concentration of shopping malls, whereas cluster 0 has low to no number of malls. Opening a mall in cluster 1 would be a risky decision, as there would be strong competition from the preexisting shopping centres. Looking at cluster 2, which has a moderate concentration of malls, opening a new mall in these places may or may not be a successful decision. For example, perhaps a unique propsition for a mall would be more profitable than a mall similar to the ones already present in the neighbourhood. 

Coming to cluster 0, where each neighbourhood likely contains at most 1 or 2 malls, other factors still need to be considered before developers decide on building a new mall. Firstly, it may be so that instead of the concept of a single shopping centre, the neighbourhood has a more distributed layout for their facilties, with shops, restaurants and recreational areas, etc. being spread out rather than present in a single building. The residents of the neighbourhood may already be satisfied with this layout. Secondly, the neighbourhood may be too small, and a mall may not be feasible to build in the long run. Another reason could be that a cluster 0 neighbourhood is close to a cluster 1 neighbourhood, so residents of cluster 0 need only travel a short distance to visit a mall. Therefore, a further analysis still needs to be done, perhaps in the form of surveys, or just like this project but with other factors. However, we have certainly found those places that property developers should avoid when planning a new building project for a shopping mall.